# Setup

## Import Libraries

In [1]:
import pathlib
import sys
import os
import platform

import requests

import pandas as pd
import numpy as np
import geopandas as gpd
#import contextily as cx

import seaborn as sns

import time
import datetime

import statsmodels.api as sm

import logging

from matplotlib.backends.backend_pdf import PdfPages
import matplotlib.pyplot as plt
import matplotlib.dates as dates
import matplotlib.dates as mdates
import matplotlib.gridspec as gridspec
import matplotlib
import matplotlib as mpl
import matplotlib.cm as cm
%matplotlib inline

In [2]:
print("Operating System " + platform.system() + " " + platform.release())
print("Python Version " + str(sys.version))
print("Numpy Version " + str(np.__version__))
print (os.environ['CONDA_DEFAULT_ENV'])

Operating System Windows 11
Python Version 3.13.1 | packaged by conda-forge | (main, Jan 13 2025, 09:37:28) [MSC v.1942 64 bit (AMD64)]
Numpy Version 2.2.2
py313


## Import paths

In [3]:
gispath = pathlib.Path("G:/Shared Drive/UGS_Flux/Projects_and_Proposals/Castledale_ET/")
ctnpath = gispath / "Cottonwood"
dlypath = ctnpath / "openet_daily_data"
timepath = ctnpath / "openet_data"
dlyapipath = ctnpath / "openet_daily_api"
dlyflws = ctnpath / "daily_flows"

## Import API keys

In [4]:
sys.path.append("G:/My Drive/Python/")

import dbconnect

## Import custom scripts

In [5]:
import sys
import pathlib
sys.path.append("G:/Shared Drives/UGS_Flux/Data_Processing/Jupyter_Notebooks/Cottonwood")
import cottonwood_calc


# Pull in GIS Data

In [6]:
gispath = pathlib.Path("G:/Shared Drives/UGS_Flux/Projects_and_Proposals/Castledale_ET/")
ecdb = gispath / "cottonwood_meters.gdb"
pou = gpd.read_file(ecdb, driver='FileGDB', layer='placeofuse_albers') 

# Reproject to a projection that preserves area
pou = pou.to_crs("EPSG:6350")

# Create dictionaries that match field ID to meter number and area
meternumbers = pou[['ID','Meternumber']].set_index('ID').to_dict()['Meternumber']
pou['acres'] = pou.geometry.area * 0.000247105
acrenums = pou[['ID','acres']].set_index('ID').to_dict()['acres']

# dissolve by meter
pou_diss = pou.dissolve(by='Meternumber').drop(['Shape_Length', 'Shape_Area','Acreage','ID'],axis=1)


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\pyogrio\raw.py:198: RuntimeWarning: driver OpenFileGDB does not support open option DRIVER
  return ogr_read(


In [7]:
pou_diss.loc['CW21']

geometry           MULTIPOLYGON Z (((-1283858.4587086716 1900858....
irr_area                                             Clipper Western
fld_comnt                                                       None
ft_from_crk                                                7709.3012
ft_city_service                                          2068.405609
SoilClass                                                          B
AWC                                                            20.74
avg_elev                                                     5905.56
irr_type                                                       pivot
acres                                                       85.57856
Name: CW21, dtype: object

# OpenET API to download Daily ET data

* [Documentation](https://open-et.github.io/docs/build/html/index.html)
* [Swagger Docs](https://openet-api.org/) 
* [API Key Found Here](https://account.etdata.org/settings/profile)

In [8]:
api_key = dbconnect.openetapi()

pathlib.Path("./test/").mkdir(parents=True, exist_ok=True)

testpath = pathlib.Path("./test/")

oet = cottonwood_calc.OpenET_Download(api_key=api_key, gpd_df=pou_diss, save_loc=testpath, interval='daily')

Station BC14 not in geographic file.
Station CW7 not in geographic file.
Station CW12 not in geographic file.
Station CW30 not in geographic file.
Station LM1 not in geographic file.
Station LM33 not in geographic file.
Station LM74 not in geographic file.
Station MD_51_Repeater not in geographic file.
Station UM6 not in geographic file.
Station UM9 not in geographic file.
Station UM33 not in geographic file.
Station UM42 not in geographic file.
Station UM51 not in geographic file.


In [9]:
oet.geographic_data

geometry       irr_area  \
Meternumber                                                                     
BC1          POLYGON Z ((-111.03854 39.2134 0, -111.03861 3...       Blue Cut   
BC10         POLYGON Z ((-111.02874 39.20402 0, -111.02443 ...       Blue Cut   
BC11         POLYGON Z ((-111.02258 39.20593 0, -111.02111 ...       Blue Cut   
BC12         POLYGON Z ((-111.03826 39.20455 0, -111.03676 ...       Blue Cut   
BC13         POLYGON Z ((-111.03758 39.19842 0, -111.03624 ...           None   
...                                                        ...            ...   
UM55         POLYGON Z ((-111.05138 39.23657 0, -111.05144 ...  Upper Mammoth   
UM56         POLYGON Z ((-111.08055 39.24638 0, -111.07996 ...  Upper Mammoth   
UM6&9        POLYGON Z ((-111.07505 39.24789 0, -111.07387 ...  Upper Mammoth   
UM7          POLYGON Z ((-111.07488 39.24812 0, -111.07443 ...  Upper Mammoth   
UM8          MULTIPOLYGON Z (((-111.07864 39.24627 0, -111....  Upper Mammoth   

                          fld_comnt  ft_from_crk  ft_city_service SoilClass  \
Meternumber                                                                   
BC1           looks fallowed in hex   578.857846      1354.277446         C   
BC10                           None  2377.461232      2003.263075         C   
BC11                           None    28.412892         0.000000         C   
BC12                           None  4070.964794      3096.545734         C   
BC13             mixed uses; patchy  5814.415801      4268.077518         D   
...                             ...          ...              ...       ...   
UM55                           None  2252.809805         0.000000         B   
UM56                           None     5.477679      1037.077025         B   
UM6&9                          None    79.801534       222.438035         B   
UM7                            None   780.735020       915.475878         B   
UM8          all along the boundary   231.230650      1198.836649         B   

               AWC  avg_elev irr_type       acres  
Meternumber                                        
BC1          18.12   5698.56     line   10.636621  
BC10         20.20   5666.76     line   17.416872  
BC11         16.46   5633.38     line   20.601822  
BC12         15.76   5716.66    pivot  123.894042  
BC13         10.18   5674.18     line   98.481314  
...            ...       ...      ...         ...  
UM55         21.11   5804.78     line    3.550355  
UM56         21.26   5885.68     line   23.477000  
UM6&9        22.53   5862.74     line   11.072819  
UM7          22.80   5877.63     line    2.866422  
UM8          21.54   5894.29     line   32.286197  

[179 rows x 10 columns]

## Daily Data

In [21]:
oet.scrape_all()

C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'utah.openet-api.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


[{'time': '2016-01-01', 'eto': 0.017}, {'time': '2016-01-02', 'eto': 0.017}, {'time': '2016-01-03', 'eto': 0.017}, {'time': '2016-01-04', 'eto': 0.02}, {'time': '2016-01-05', 'eto': 0.02}, {'time': '2016-01-06', 'eto': 0.02}, {'time': '2016-01-07', 'eto': 0.013}, {'time': '2016-01-08', 'eto': 0.02}, {'time': '2016-01-09', 'eto': 0.021}, {'time': '2016-01-10', 'eto': 0.02}, {'time': '2016-01-11', 'eto': 0.018}, {'time': '2016-01-12', 'eto': 0.016}, {'time': '2016-01-13', 'eto': 0.02}, {'time': '2016-01-14', 'eto': 0.017}, {'time': '2016-01-15', 'eto': 0.023}, {'time': '2016-01-16', 'eto': 0.023}, {'time': '2016-01-17', 'eto': 0.033}, {'time': '2016-01-18', 'eto': 0.025}, {'time': '2016-01-19', 'eto': 0.023}, {'time': '2016-01-20', 'eto': 0.03}, {'time': '2016-01-21', 'eto': 0.027}, {'time': '2016-01-22', 'eto': 0.027}, {'time': '2016-01-23', 'eto': 0.023}, {'time': '2016-01-24', 'eto': 0.03}, {'time': '2016-01-25', 'eto': 0.033}, {'time': '2016-01-26', 'eto': 0.03}, {'time': '2016-01-27

C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'utah.openet-api.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


[{'time': '2017-01-01', 'eto': 0.012}, {'time': '2017-01-02', 'eto': 0.018}, {'time': '2017-01-03', 'eto': 0.031}, {'time': '2017-01-04', 'eto': 0.031}, {'time': '2017-01-05', 'eto': 0.01}, {'time': '2017-01-06', 'eto': 0.021}, {'time': '2017-01-07', 'eto': 0.012}, {'time': '2017-01-08', 'eto': 0.011}, {'time': '2017-01-09', 'eto': 0.017}, {'time': '2017-01-10', 'eto': 0.028}, {'time': '2017-01-11', 'eto': 0.041}, {'time': '2017-01-12', 'eto': 0.034}, {'time': '2017-01-13', 'eto': 0.023}, {'time': '2017-01-14', 'eto': 0.031}, {'time': '2017-01-15', 'eto': 0.03}, {'time': '2017-01-16', 'eto': 0.043}, {'time': '2017-01-17', 'eto': 0.028}, {'time': '2017-01-18', 'eto': 0.023}, {'time': '2017-01-19', 'eto': 0.02}, {'time': '2017-01-20', 'eto': 0.028}, {'time': '2017-01-21', 'eto': 0.034}, {'time': '2017-01-22', 'eto': 0.034}, {'time': '2017-01-23', 'eto': 0.034}, {'time': '2017-01-24', 'eto': 0.034}, {'time': '2017-01-25', 'eto': 0.031}, {'time': '2017-01-26', 'eto': 0.021}, {'time': '2017

C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'utah.openet-api.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


...

MD43 2021
MD43 2022


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'utah.openet-api.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
ERROR:root:An exception was thrown!
Traceback (most recent call last):
  File "G:\Shared Drives/UGS_Flux/Data_Processing/Jupyter_Notebooks/Cottonwood\cottonwood_calc\web_scrape.py", line 186, in scrape_et_polygons
    dfs[year] = pd.DataFrame(resp.json())
                ~~~~~~~~~~~~^^^^^^^^^^^^^
  File "C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\pandas\core\frame.py", line 778, in __init__
    mgr = dict_to_mgr(data, index, columns, dtype=dtype, copy=copy, typ=manager)
  File "C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\pandas\core\internals\construction.py", line 503, in dict_to_mgr
    return arrays_to_mgr(arrays, colu

MD43 2022
MD43 2023


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'utah.openet-api.org'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
ERROR:root:An exception was thrown!
Traceback (most recent call last):
  File "G:\Shared Drives/UGS_Flux/Data_Processing/Jupyter_Notebooks/Cottonwood\cottonwood_calc\web_scrape.py", line 186, in scrape_et_polygons
    dfs[year] = pd.DataFrame(resp.json())
                ~~~~~~~~~~~~^^^^^^^^^^^^^
  File "C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\pandas\core\frame.py", line 778, in __init__
    mgr = dict_to_mgr(data, index, columns, dtype=dtype, copy=copy, typ=manager)
  File "C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\pandas\core\internals\construction.py", line 503, in dict_to_mgr
    return arrays_to_mgr(arrays, colu

MD43 2023


## Monthly Data

In [ ]:
oet.interval = 'monthly'
oet.start_yr = 2000
oet.save_loc = pathlib.Path("./monthly_openet/")

oet.scrape_all()


In [ ]:
pd.concat(station_dfs)#.to_csv(ctnpath / 'combined_daily_openet_data.csv')

In [ ]:
pd.read_csv(testpath / "combined_daily_openet_ETo_LM20.csv")

https://www.fao.org/3/X0490E/x0490e0c.htm

In [ ]:
sites = []
for file in testpath.glob("*.csv"):  
    sites.append(str(file.name).split("_")[-1].split(".")[0])
sites = list(set(sites))

site_data = {}

for site in sites:
    varib_data = {}
    for file in testpath.glob("*.csv"):
        site_check = str(file.name).split("_")[-1].split(".")[0]
        if site == site_check:
            varib = str(file.name).split("_")[-2]
            varib_data[f"{varib}"] = pd.read_csv(file,index_col='time',parse_dates=True)
            
    site_data[site] = pd.concat(varib_data,axis=1)

In [ ]:
sites

In [ ]:
openet_daily = pd.concat(site_data).droplevel(level=1,axis=1)
openet_daily = openet_daily.reset_index().rename(columns={'level_0':'station','time':'DateTime'})

In [ ]:
openet_daily.to_parquet(ctnpath / "openet_daily.parquet")

# OpenET data manually downloaded from the site

In [ ]:
dfs = {}

for file in dlypath.glob("openet_daily*"):
    print(file.name)
    year = file.name.split(".")[0].split("_")[-1]
    station = file.name.split(".")[0].split("_")[-2]
    df = pd.read_csv(file,index_col="DateTime",parse_dates=True)
    df['year'] = year
    df['station'] = station
    dfs[f"{year}-{station}"] = df
    
oet_daily = pd.concat(dfs).reset_index()#.set_index('DateTime')
oet_daily = oet_daily.drop(['level_0','ET Units', 'Source','Method'],axis=1)
oet_daily = oet_daily.set_index(['station','DateTime'])

In [ ]:
oet_daily

In [ ]:
pou_diss['acres'] = pou_diss.loc['UM23'].geometry.area * 0.000247105
oet_daily_sp = pd.merge(pou_diss.reset_index(), openet_daily.reset_index(), left_on='Meternumber',right_on='station')

oet_daily_sp['Ens. ET (ac-ft)'] = (oet_daily_sp['etEns']*oet_daily_sp["acres"]*0.0833333)
oet_daily_sp['Precip (ac-ft)'] = oet_daily_sp['PR']*oet_daily_sp["acres"]*0.0833333
oet_daily_sp['Effective ET (ac-ft)'] = oet_daily_sp['Ens. ET (ac-ft)'] - oet_daily_sp['Precip (ac-ft)']
oet_daily_sp = oet_daily_sp.set_index(['Meternumber','DateTime'])


In [ ]:

oet_daily_sp.loc["BC1",'NDVI'].plot()
oet_daily_sp.loc["BC22",'NDVI'].plot()
oet_daily_sp.loc["BC29",'NDVI'].plot()
oet_daily_sp.loc["CW25",'NDVI'].plot()
plt.ylabel('NDVI')
plt.title("BC1")

# Flowmeter data

In [ ]:
# Hand-entered annual totalizer readings
meter_read = pd.read_excel(ctnpath / 'IRR_totals.xlsx')
#meter_read['sensor-year'] = meter_read[['sensor','year']].apply(lambda x: f"{x[0]}_{x[1]}",1)
meter_read= meter_read.set_index(['sensor','year']).sort_index()
meter_read

## Create index of station values

directory of html files copied from Emery WCD website http://www.ewcd.org/canals/


In [10]:
# initiate class
irdata = cottonwood_calc.web_scrape.irr_scrape()
# directory of html files copied from Emery WCD website http://www.ewcd.org/canals/
#html_file_dir = pathlib.Path("C:/Users/paulinkenbrandt/PycharmProjects/Cottonwood/data/html_files")
html_file_dir = pathlib.Path("G:/Shared Drives/UGS_Flux/Data_Processing/Jupyter_Notebooks/Cottonwood/data/html_files")

# pull in station lists
gpm_stations, gpm_numbers, acft_stations, acft_numbers = irdata.scrape_station_lists(html_file_dir)

Adding path


In [11]:
gpm_numbers

{'CW21': '11054',
 'CW13': '11057',
 'CW41': '11060',
 'CW12': '11063',
 'CW27': '11066',
 'CW48': '11069',
 'CW49': '11072',
 'CW53': '11075',
 'CW61': '11078',
 'CW60': '11081',
 'CW54': '11172',
 'CW55': '11178',
 'CW58': '11184',
 'CW59': '11190',
 'CW62': '11196',
 'CW65': '11202',
 'CW66': '11208',
 'CW67': '11214',
 'CW30': '11269',
 'CW32': '11275',
 'CW33': '11281',
 'CW36': '11287',
 'CW38': '11293',
 'CW40': '11299',
 'CW43': '11305',
 'CW47': '11311',
 'CW51': '11317',
 'CW52': '11323',
 'CW4': '11356',
 'CW6': '11362',
 'CW7': '11368',
 'CW8': '11374',
 'CW10': '11380',
 'CW11': '11386',
 'CW29': '11392',
 'CW39': '11398',
 'CW42': '11404',
 'CW44': '11410',
 'CW68': '11416',
 'UM56': '11428',
 ' CW5': '11470',
 'CW1': '11563',
 'CW1B': '11569',
 'BC1': '11575',
 'BC4': '11581',
 'BC5': '11587',
 'BC6': '11593',
 'BC20': '11599',
 'BC21': '11605',
 'BC34': '11611',
 'BC36': '11617',
 'UM1': '11745',
 'UM3': '11751',
 'UM53': '11757',
 'CW19': '11763',
 'CW24': '11769',
 'C

## Download station data

commented out b/c takes a while and has been done already; uncomment to rerun

In [19]:
irdata.scrape_meters()
irdata.scrape_meters(pullvalues='acft')

C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app.exactraq.net'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


CW16 12627


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app.exactraq.net'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


UM26 12633


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app.exactraq.net'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


...

CW71 13688


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app.exactraq.net'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


LM28 13723


C:\Users\paulinkenbrandt\.conda\envs\py313\Lib\site-packages\urllib3\connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'app.exactraq.net'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


LM33 13729


## Aggregate acft data

In [20]:
irdata.acft_save_dir

WindowsPath('../ctnpath/ewcd_api_download_acft')

In [ ]:
-111.00826263427736,39.20148117163808,-111.00963592529298,39.20073290071608,-111.0096573829651,39.200217420555454,-111.00843429565431,39.19926959232421,-111.00907802581787,39.198937017984335,-111.0097861289978,39.198770730224005,-111.01002216339113,39.198454782395025,-111.01006507873537,39.19614333137351,-111.00974321365358,39.19551141066369,-111.0085415840149,39.19521207781749,-111.00723266601564,39.19567770613834,-111.00646018981935,39.196442660252394,-111.00564479827882,39.19704131418449,-111.00564479827882,39.19750693038292,-111.0053873062134,39.197806253452455,-111.00264072418214,39.198355009101206,-111.00291967391969,39.19916982018758,-111.00388526916504,39.20028393433712,-111.0050654411316,39.20076615737077,-111.00628852844238,39.20128163350487,-111.00736141204834,39.201514427938505

In [ ]:
site_id = "BC28"

metdata = {}

ctnpath = pathlib.Path("G:/Shared drives/UGS_Groundwater/Projects/Eddy_Covariance/GIS/Cottonwood/Daily_Flow_Compilation")

for file in ctnpath.glob(f"{site_id}/*sensor*"):
    #print(file.name)
    #meter_id = file.name.split(".")[0].split("_")[-1]
    meter_id = file.name.split(".")[0]
    df = pd.read_csv(file,names=['datetime','gpm','recnum','notes','pgID'],skiprows=1)
    df['gpm'] = pd.to_numeric(df['gpm'],errors="coerce")
    df['datetime'] = pd.to_datetime(df['datetime'],utc=True)
    df = df.set_index(['datetime'])
    df.index = df.index.tz_convert("MST").tz_localize(None)
    df = df.sort_index()
    df = df.resample('1H').mean(numeric_only=True).interpolate(method='time')

    metdata[meter_id] = df

meter_gpm = pd.concat(metdata)
#meter_acft['year'] = meter_acft.index.get_level_values(1).year
meter_gpm = meter_gpm.reset_index()#.rename(columns={'level_0': 'meternumber'})
meter_gpm['meternumber'] = meter_gpm['level_0'].str.split("_",n=1).str[0]

#meter_acft_yr = meter_acft.groupby(['meternumber','year']).max()
#meter_acft_yr
for col in ['level_0','recnum','notes','meternumber','pgID']:
    if col in meter_gpm.columns:
        meter_gpm = meter_gpm.drop([col],axis=1)
meter_gpm = meter_gpm.set_index('datetime')
flow_hr = meter_gpm.loc[pd.to_datetime('2023-01-01'):pd.to_datetime('2023-11-01')].resample('1H').asfreq().interpolate()
flow_hr['acft'] = flow_hr['gpm']*60*3.06889e-6 # gpm to gph to ac-ft/hr
flow = flow_hr.resample('1D').sum() # ac-ft/day
flow.to_parquet(ctnpath / f"{site_id}.parquet")

In [ ]:
#%matplotlib notebook
#%matplotlib widget
import matplotlib.animation as animation
from matplotlib.dates import DateFormatter





#plt.twinx()
#oet_b28['Ensemble ET'].plot(color='red')
#oet_b28['Precip (gridMET)'].plot(color='green')

oet = {}
flows = {}

site_ids = ['BC22','BC28']

timesteps = ['2023-03-18','2023-04-07','2023-04-17','2023-04-27','2023-05-02','2023-05-22',
             '2023-06-26','2023-07-01','2023-07-06','2023-07-11','2023-07-16','2023-07-21',
             '2023-08-05','2023-08-15','2023-08-30','2023-09-19','2023-09-24','2023-09-29',
             '2023-10-04','2023-10-09','2023-10-19','2023-10-24','2023-10-29','2023-11-08','2023-11-28']
timesteps = pd.to_datetime(timesteps)

fig, ax = plt.subplots(2,1,sharex=True)

ax2 = {}
line1 = {}
line2 = {}
line3 = {}
label = {}


i=0
for site_id in site_ids:

    flows[site_id]= pd.read_parquet(ctnpath / f"{site_id}.parquet")
    
    oet[site_id] = pd.read_csv(ctnpath / f"openet_{site_id}.csv",parse_dates=True,index_col='DateTime')

    if i == 0:
        lab1 = 'OpenET ens ET'
        lab2 = 'Gridmet Precip'
        lab3 = 'Diversion'
    else:
        lab1 = None
        lab2 = None
        lab3 = None
    line1[i], = ax[i].plot(oet[site_id].index[0], oet[site_id].iloc[0]['Ensemble ET'],label=lab1,color='red',zorder=1)
    line2[i], = ax[i].plot(oet[site_id].index[0], oet[site_id].iloc[0]['Precip (gridMET)'],label=lab2,color='green',alpha=0.5,zorder=2)
    
    ax2[i] = ax[i].twinx()
    line3[i], = ax2[i].plot(flows[site_id].index[0],flows[site_id].iloc[0]['acft'],color='blue',alpha=0.5,zorder=10,label=lab3)

    ax[i].set_title(site_id)
    
    
    ax2[i].set_ylim(0,5)
    ax2[i].set_ylabel("Pumping (acft/day)")
    ax[i].set_ylabel("Precip and ET (in/day)")
    i+=1
    ## Rotate date labels automatically
    #fig.autofmt_xdate()
myFmt = DateFormatter("%b")
label = ax[0].text(pd.to_datetime('2023-09-20'),0.5, f"{timesteps[0]:%Y-%m-%d}",fontsize=12,
                     color="black",zorder=0)
fig.legend(loc='outside upper center',ncols=3)
ax[1].xaxis.set_major_formatter(myFmt)
ax[1].set_xlim(pd.to_datetime("2023-01-01"),pd.to_datetime("2023-12-01"))
ax[1].set_xlabel('Month')


def update(frame):
    # for each frame, update the data stored on each artist.
    for j in [0,1]:
        line1[j].set_xdata(oet[site_ids[j]].loc[:timesteps[frame]].index)
        line1[j].set_ydata(oet[site_ids[j]].loc[:timesteps[frame],'Ensemble ET'])
        line2[j].set_xdata(oet[site_ids[j]].loc[:timesteps[frame]].index)
        line2[j].set_ydata(oet[site_ids[j]].loc[:timesteps[frame],'Precip (gridMET)'])
        line3[j].set_xdata(flows[site_ids[j]].loc[:timesteps[frame]].index)
        line3[j].set_ydata(flows[site_ids[j]].loc[:timesteps[frame],'acft'])
    label.set_text(f"{timesteps[frame]:%Y-%m-%d}")
    return (line1[0],line1[1], line2[0],line2[1], line3[0],line3[1], label)


anim = animation.FuncAnimation(fig=fig, func=update, frames=len(timesteps), interval=1000)

anim.save(filename= ctnpath / "twosites.gif", writer="pillow")
plt.show()

In [ ]:
metdata = {}

ctnpath = pathlib.Path("G:/Shared drives/UGS_Groundwater/Projects/Eddy_Covariance/Data_Processing/Jupyter_Notebooks/ctnpath/ewcd_api_download")

for file in irdata.acft_save_dir.glob("*"):
    #print(file.name)
    #meter_id = file.name.split(".")[0].split("_")[-1]
    meter_id = file.name.split(".")[0]
    df = pd.read_csv(file,names=['datetime','acft','recnum','notes','pgID'],skiprows=1)
    df['acft'] = pd.to_numeric(df['acft'],errors="coerce")
    df['datetime'] = pd.to_datetime(df['datetime'],utc=True)
    df = df.set_index(['datetime'])
    df.index = df.index.tz_convert("MST").tz_localize(None)
    df = df.sort_index()
    df = df.resample('1H').mean(numeric_only=True).interpolate(method='time')

    metdata[meter_id] = df

meter_acft = pd.concat(metdata)
meter_acft['year'] = meter_acft.index.get_level_values(1).year
meter_acft = meter_acft.reset_index()#.rename(columns={'level_0': 'meternumber'})
meter_acft['meternumber'] = meter_acft['level_0'].str.split("_",n=1).str[0]

meter_acft_yr = meter_acft.groupby(['meternumber','year']).max()
meter_acft_yr

In [ ]:
meter_acft.loc["BC26"]

## Combine downloaded files

In [ ]:
#flow_dir = pathlib.Path("G:/Shared drives/UGS_Groundwater/Projects/Eddy_Covariance/GIS/Cottonwood/ewcd_api_download/")
# combine downloaded files
meter_gpm = irdata.combine_flow_files()

# summarize to yearly values
meter_gpm_yr = irdata.summarize_gpm_to_yearly()

In [ ]:
meter_gpm = meter_gpm.set_index(['meternumber','datetime'])

In [ ]:

meter_gpm.loc['BC24','gpm'].plot()

In [ ]:
comparison = pd.concat([meter_gpm_yr['gpm_total_acft'],meter_acft_yr['acft']],axis=1).dropna()
comparison.to_csv(ctnpath / 'gage_reading_comparison.csv')


## Compare Annual to Instantanous flow Values

In [ ]:
comparison = pd.read_csv(ctnpath / 'gage_reading_comparison.csv')


comparison['residual'] = comparison['acft'] - comparison['gpm_total_acft']
#comp_filtered = comparison[comparison['total_acft']<750]


df = comparison.sort_values('gpm_total_acft').dropna()
#define predictor and response variables
x = df['gpm_total_acft']
y = df['acft']

#add constant to predictor variables
X = sm.add_constant(x)

#fit linear regression model
res = sm.RLM(y, X).fit()
#predictions = res.get_prediction()




comp_out = comparison[comparison['residual'].abs() > 100]
comparison['gpm_total_acft']

low_err = comparison[(comparison['residual'].abs()<10)&(comparison['acft'] > 0)].rename(columns={'Unnamed: 0':'sensor'})
#low_err['sens_yr'] = low_err[['sensor','year']].apply(lambda x: f"{x[0]}-{x[1]}",1)
#low_err_sensors = low_err['sens_yr'].unique()

df1 = low_err.sort_values('gpm_total_acft').dropna()
#define predictor and response variables
x1 = df1['gpm_total_acft']
y1 = df1['acft']

#add constant to predictor variables
X1 = sm.add_constant(x1)

#fit linear regression model
res1 = sm.RLM(y1, X1).fit()
#predictions = res.get_prediction()

fig, ax = plt.subplots(2,1,figsize=(8,10),sharex=True)

ax[0].scatter(x,y,color='orange',s=10,label='all flow comparison data')

ax[0].scatter(comp_out['gpm_total_acft'],comp_out['acft'],zorder=0,color='blue',label='exceed 10 ac-ft/yr difference')

linx = range(0,500)
ax[0].plot(linx,linx,color='grey',linestyle=":",label='1:1 line')
ax[1].plot(linx,linx,color='grey',linestyle=":",label='1:1 line')
ax[0].plot(x, res.fittedvalues, 'r--', label="OLS")
ax[0].scatter(None,None,zorder=0,color='green',label='filtered measurements')

ax[0].grid()
ax[1].grid()
ax[1].scatter(low_err['gpm_total_acft'],low_err['acft'],zorder=0,color='green',label='filtered measurements')
ax[1].set_ylim(-10,600)
ax[0].set_xlim(-10,600)
ax[1].plot(x1, res1.fittedvalues, 'r--', label="OLS")
ax[1].set_xlabel('Cumulative hourly readings (ac-ft)')
ax[0].set_ylabel('Totalizer readings (ac-ft)')
ax[1].set_ylabel('Totalizer readings (ac-ft)')
ax[0].legend(loc=4)

In [ ]:
res.summary()

In [ ]:
comparison

In [ ]:
(comparison['residual']/comparison['gpm_total_acft'])

In [ ]:

df = comparison.sort_values('gpm_total_acft').dropna()
#define predictor and response variables
x = df['gpm_total_acft']
y = df['acft']

g = sns.jointplot(x='gpm_total_acft', y='acft', data=df,
                  kind="reg", truncate=False,
                  xlim=(0, 600), ylim=(0, 600),
                  color="m", height=7)

In [ ]:
res.summary()

In [ ]:
sns.histplot(data=comparison, x='residual', kde=True)
plt.xlim(-100,100)
#plt.ylim(0,100)
plt.grid()

In [ ]:
MAE, MSE, RMSE, 

In [ ]:
comparison[comparison['residual'].abs() > 70].hist()